In [1]:
# These are the imports of the McsData module
import sys, importlib
import McsPy.McsData
import McsPy.McsCMOS
from McsPy import ureg, Q_

import numpy as np
from scipy.stats.mstats import zscore

import matplotlib.pyplot as plt
import plotly
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
plotly.offline.init_notebook_mode(connected=True)
import gc
import random
import tables
import pandas as pd

In [2]:
# for group in h5file.walk_groups("/"):
#     for array in h5file.list_nodes(group, classname='Array'):
#         print(array)

In [3]:
pathfile = "/home/labs/rivlinlab/bndolev/MEAdata/database/user=ND/date=2019-03-12/tissue=retina/type=systemcalibration/eye=left/MEAnumber=17079/run=1/2019-03-12T13-54-57Retina_Trial4.h5"
raw_data = McsPy.McsData.RawData(pathfile)
h5file = tables.open_file(pathfile, mode= 'r',driver="H5FD_CORE")
sync_table = h5file.root.Data.Recording_0.AnalogStream.Stream_0.ChannelData
raw_chan_table = h5file.root.Data.Recording_0.AnalogStream.Stream_0.ChannelData
raw_chan_data = raw_chan_table.read()
channel_id = list(raw_data.recordings[0].analog_streams[0].channel_infos.keys())
print(raw_chan_data.shape)

Recording_0 <HDF5 group "/Data/Recording_0" (2 members)>
Stream_0 <HDF5 group "/Data/Recording_0/AnalogStream/Stream_0" (3 members)>
ChannelData <HDF5 dataset "ChannelData": shape (252, 20112000), type "<i4">
ChannelDataTimeStamps <HDF5 dataset "ChannelDataTimeStamps": shape (1, 3), type "<i8">
InfoChannel <HDF5 dataset "InfoChannel": shape (252,), type "|V104">
Stream_1 <HDF5 group "/Data/Recording_0/AnalogStream/Stream_1" (3 members)>
ChannelData <HDF5 dataset "ChannelData": shape (2, 20112000), type "<i4">
ChannelDataTimeStamps <HDF5 dataset "ChannelDataTimeStamps": shape (1, 3), type "<i8">
InfoChannel <HDF5 dataset "InfoChannel": shape (2,), type "|V104">
(252, 20112000)


In [4]:
data = {'channel':[], 'raw':[]}
start = int(3.02e06) #0
stop = int(3.04e06) #analog_stream_data.shape[0]
R = round((stop-start)/2)
if (R<=0):
    R=1
def downsample(R,input_arr):
    split_arr = np.linspace(0, input_arr.shape[0], num=R+1, dtype=int)
    dwnsmpl_subarr = np.split(input_arr, split_arr[1:])
    dwnsmpl_arr = np.array( list( np.mean(item) for item in dwnsmpl_subarr[:-1] ) )
    return(dwnsmpl_arr)

x = np.arange(start,stop)
numchannels = 5
channelchoices = random.sample(range(0,len(channel_id)),numchannels)

for chan in range(0,numchannels):
    
    trace2 = go.Scattergl(
        x = downsample(R, x),
        y = downsample(R,zscore(raw_chan_data[channelchoices[chan],start:stop]))+chan*3,
        mode = 'lines',
        name = 'Raw Electrode %d' % channel_id[channelchoices[chan]],
        opacity=.5
    )
    data['channel'].append(channel_id[chan])
    data['raw'].append(trace2)
gc.collect() 

7

In [5]:
iplot([m for m in data['raw']])